In [1]:
import os
import zipfile
import tempfile
import xml.etree.ElementTree as ET
import pandas as pd
from tqdm import tqdm
from HCFA_XML_to_DF import *

In [2]:
import gc
gc.collect()

0

In [3]:
Hcfa_key_list = pd.read_excel("/Data/XELP_Experiments/Notebooks/HCFA_Keys.xlsx")
Hcfa_key_list.head(3)

Key_Name
0          MissApp
1  Box19B_Provider
2       Box19B_NPI

In [4]:
key_list = Hcfa_key_list['Key_Name'].unique()


In [5]:
Trans_dir = '/Data/XELP_Experiments/Training_Data/HCFA/Extracted_EV_GRPBX/TRANS/'
trans_files_list = os.listdir(Trans_dir)
print(len(trans_files_list))

15000


In [6]:
gc.collect()

977

In [7]:
data = pd.DataFrame()
i = 0
for each_trans_file in tqdm(trans_files_list):
    each_trans_path = os.path.join(Trans_dir, each_trans_file)
    #print(each_trans_path)
    df, im_names = OCR_XML_to_DataFrame(each_trans_path, key_list)
    #print(df.shape)
    
    i += 1
    df["Trans_file_name"] = each_trans_file
    #print(im_names)
    df["img_details"] = [im_names] * len(df)
    data  = pd.concat([data, df], ignore_index=True)

    if i%200 == 0:
        gc.collect()


100%|███████████████████████████████████| 15000/15000 [3:09:45<00:00,  1.32it/s]


In [57]:
data.columns

Index(['Data', 'TRANS_Value', 'Group_name', 'Image_width', 'Image_height',
       'Field_Name', 'x1', 'x2', 'y1', 'y2', 'Page', 'OCR_OMNI', 'OCR_IGEAR',
       'OCR_AT', 'OCR_Optimizer', 'Comments', 'Trans_file_name',
       'img_details'],
      dtype='object')

In [58]:
data.shape

(4371082, 18)

In [59]:
pd.set_option("display.max_rows", None)

In [52]:
data[3553:3557]['img_details']

3553    [1378N430MC010_002.tiff, 1378N430MC010_003.tif...
3554    [1378N430MC010_002.tiff, 1378N430MC010_003.tif...
3555    [1378N430MC010_002.tiff, 1378N430MC010_003.tif...
3556    [1378N430MC010_002.tiff, 1378N430MC010_003.tif...
Name: img_details, dtype: object

In [66]:
#data.to_excel("/Data/XELP_Experiments/Training_Data/HCFA/EDA_Analysis/EV_GRPBMX.xlsx", index=False)

In [82]:
data.to_parquet("/Data/XELP_Experiments/Training_Data/HCFA/EDA_Analysis/EV_GRPBX.parquet", index=False)